# Heatmap der Sterberaten in der Schweiz und in Frankreich

Diese Visualisierungen sind Reproduktionen der sehr schönen und informativen Heatmaps, die Kieran Healy am [4. Dezember 2018 auf seinem Blog](https://kieranhealy.org/blog/archives/2018/12/04/heatmaps-of-mortality-rates/) veröffentlicht hat. Kieran Healy hat die Grafiken mit R und ggplot2 erstellt. Ich habe [Panda](http://pandas.pydata.org/) und [Bokeh](https://bokeh.pydata.org) verwendet.

In [1]:
# Imports & settings
from bokeh.plotting import figure, ColumnDataSource
from bokeh.io import output_notebook, output_file, show
from bokeh.palettes import magma
from bokeh.transform import linear_cmap
from bokeh.layouts import Column
from bokeh.embed import components
import numpy as np
import pandas as pd

output_notebook()

Loading BokehJS ...

In [2]:
# data import
df_fr = pd.read_csv('data/Death rate/France_Mx_1x1.txt', header=1, sep='\s+', na_values='.', dtype={'Female': float, 'Male': float})
df_ch = pd.read_csv('data/Death rate/SwitzerlandMx_1x1.txt', header=1, sep='\s+', na_values='.', dtype={'Female': float, 'Male': float})

# concatenate the labeled datasets
df_fr['Country'] = 'France'
df_ch['Country'] = 'Switzerland'
df = pd.concat([df_ch, df_fr])

In [3]:
df.head()

Year Age    Female      Male     Total      Country
0  1876   0  0.226663  0.280796  0.253961  Switzerland
1  1876   1  0.038919  0.035824  0.037366  Switzerland
2  1876   2  0.018009  0.019696  0.018858  Switzerland
3  1876   3  0.012410  0.012623  0.012518  Switzerland
4  1876   4  0.009166  0.009499  0.009334  Switzerland

In [4]:
# limit age range to 0 - 100 years
df['Age'] = df.Age.apply(lambda x: x.replace('+', '')).astype(int)
df = df[df['Age'] < 101]

In [5]:
# replacing death rate of 0.0 within population over 80y with NaN
df.loc[(df.Country == "Switzerland") & (df.Age > 80) & (df.Female == 0.0), "Female"] = np.nan
df.loc[(df.Country == "Switzerland") & (df.Age > 80) & (df.Male == 0.0), "Male"] = np.nan

In [6]:
# discretizing rates into percentiles
df['Percentiles_m'] = pd.qcut(df.Male, q=100, labels=np.arange(0, 1, 0.01), retbins=False)
df['Percentiles_m'] = df['Percentiles_m'].astype(float)
df['Percentiles_f'] = pd.qcut(df.Female, q=100, labels=np.arange(0, 1, 0.01), retbins=False)
df['Percentiles_f'] = df['Percentiles_f'].astype(float)

In [7]:
df.tail()

Year  Age    Female      Male     Total Country  Percentiles_m  \
22296  2016   96  0.249830  0.322662  0.265590  France           0.90   
22297  2016   97  0.276655  0.356847  0.292522  France           0.92   
22298  2016   98  0.309112  0.382754  0.322505  France           0.93   
22299  2016   99  0.328251  0.437069  0.346422  France           0.95   
22300  2016  100  0.369313  0.451546  0.381999  France           0.96   

       Percentiles_f  
22296           0.88  
22297           0.90  
22298           0.91  
22299           0.92  
22300           0.94

## Mortality Rates in Switzerland
****1841-2016****

In [8]:
mx_switzerland = df[df['Country'] == 'Switzerland'] 

tt1 = [('Jahr', '$x{0.}'),
       ('Alter', '$y{0.}'),
       ('Rate', '@Percentiles_m{.00}')]
p1 = figure(title="Männer", x_axis_label='Jahr', y_axis_label='Alter', tooltips=tt1, tools="box_select, box_zoom, reset")
p1.plot_height = 480
p1.plot_width = 960
p1.rect('Year', 'Age', 1, 1, source=ColumnDataSource(mx_switzerland),
        color=linear_cmap('Percentiles_m', magma(256)[::-1], 0, 1))

tt2 = [('Jahr', '$x{0.}'),
       ('Alter', '$y{0.}'),
       ('Rate', '@Percentiles_f{.00}')]
p2 = figure(title="Frauen", x_axis_label='Jahr', y_axis_label='Alter', tooltips=tt2, tools="box_select, box_zoom, reset")
p2.plot_height = 480
p2.plot_width = 960
p2.rect('Year', 'Age', 1, 1, source=ColumnDataSource(mx_switzerland),
        color=linear_cmap('Percentiles_f', magma(256)[::-1], 0, 1))

p = Column(p1, p2)
show(p)

In [ ]:
script_m, div_m = components(p1)
script_f, div_f = components(p2)

In [ ]:
with open('data/Death rate/mx_ch960_m.js', 'w') as f:
    f.write(script_m)
    
with open('data/Death rate/mx_ch960_m.html', 'w') as f:
    f.write(div_m)
    
with open('data/Death rate/mx_ch960_f.js', 'w') as f:
    f.write(script_f)
    
with open('data/Death rate/mx_ch960_f.html', 'w') as f:
    f.write(div_f)

## Mortality Rates in France
****1816-2016****

In [9]:
mx_france = df[df['Country'] == 'France'] 

tt1 = [('Jahr', '$x{0.}'),
       ('Alter', '$y{0.}'),
       ('Rate', '@Percentiles_m{.00}')]
p1 = figure(title="Männer", x_axis_label='Jahr', y_axis_label='Alter', tooltips=tt1, tools="box_select, box_zoom, reset")
p1.plot_height = 480
p1.plot_width = 960
p1.rect('Year', 'Age', 1, 1, source=ColumnDataSource(mx_france),
        color=linear_cmap('Percentiles_m', magma(256)[::-1], 0, 1))

tt2 = [('Jahr', '$x{0.}'),
       ('Alter', '$y{0.}'),
       ('Rate', '@Percentiles_f{.00}')]
p2 = figure(title="Frauen", x_axis_label='Jahr', y_axis_label='Alter', tooltips=tt2, tools="box_select, box_zoom, reset")
p2.plot_height = 480
p2.plot_width = 960
p2.rect('Year', 'Age', 1, 1, source=ColumnDataSource(mx_france),
        color=linear_cmap('Percentiles_f', magma(256)[::-1], 0, 1))

p = Column(p1, p2)
show(p)

In [ ]:
script_m, div_m = components(p1)
script_f, div_f = components(p2)

In [ ]:
with open('data/Death rate/mx_fr960_m.js', 'w') as f:
    f.write(script_m)
    
with open('data/Death rate/mx_fr960_m.html', 'w') as f:
    f.write(div_m)
    
with open('data/Death rate/mx_fr960_f.js', 'w') as f:
    f.write(script_f)
    
with open('data/Death rate/mx_fr960_f.html', 'w') as f:
    f.write(div_f)